In [ ]:
import numpy as np
import random
from scipy.stats import norm 

t_dataset = np.arange(0, 4096, 1)

d = 4096
d_list = []
for j in range(4096):
    d += norm.rvs(loc=0, scale=10)
    d_list.append(d)
    d += 0.01*(j-d_list[max(0, j-12)])
d_dataset = np.asarray(d_list)

t_dataset = np.arange(0, d_dataset.size, 1) 

In [ ]:
t_dat_stable = t_dataset[512:4096]
d_dat_stable = d_dataset[512:4096]

# linear regression using statsmodels
#
import numpy as np
import statsmodels.api as sm

linear_fit_d = sm.OLS(np.asarray(d_dat_stable), sm.add_constant(np.asarray(t_dat_stable))).fit()

print("Fit:\n", linear_fit_d.summary())
print("\nFit params:", linear_fit_d.params, end="\n")

residual = [d_dat_stable[i] - (linear_fit_d.params[0] + linear_fit_d.params[1]*t_dat_stable[i]) for i in range(t_dat_stable.size)]

In [ ]:
import seaborn as sbn
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("t", fontsize=24, color="#322300")
ax.set_ylabel("d", fontsize=24, color="#322300")

sbn.scatterplot(x=t_dataset, y=d_dataset, color="#322300", s=20)

sbn.regplot(x=t_dat_stable, y=d_dat_stable, color='#00a0d2', order=1, \
            scatter_kws={'s':1}, ci=None, truncate=False)

sbn.regplot(x=t_dat_stable, y=residual, color='#147864', order=1, \
            scatter_kws={'s':1}, ci=None, truncate=False)

In [ ]:
import statsmodels
import statsmodels.tsa
import statsmodels.tsa.stattools

aut = statsmodels.tsa.stattools.acf(residual, nlags=512)

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("Delta t", fontsize=24, color="#322300")
ax.set_ylabel("norm. autocorr. of the residual", fontsize=24, color="#322300")

sbn.scatterplot(x=np.arange(0, aut.size, 1), y=aut, color="#322300", s=10)

In [ ]:
import math

t_log_out = np.arange(128)
log_aut = np.asarray([math.log(max(abs(x), 1.0e-04)) for x in aut[:128]])

fig, ax = plt.subplots()
fig.set_size_inches(14, 6)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("Delta t", fontsize=24, color="#322300")
ax.set_ylabel("ln rho(Delta t) for residual", fontsize=24, color="#322300")

sbn.scatterplot(x=t_log_out, y=log_aut, color="#322300", s=10)

sbn.regplot(x=t_log_out[:64], y=log_aut[:64], color='#e6503c', order=2, \
            scatter_kws={'s':1}, ci=None, truncate=False)

In [ ]:
import statsmodels.api as sm

lin_sqr_array = np.asarray([[t, t*t] for t in t_log_out[:64]])

compute_decorrelation_time = sm.OLS(log_aut[:64], lin_sqr_array).fit()

print("Statsmodels regression output:\n", compute_decorrelation_time.summary())

print("\nDecorrelation time:", -1/compute_decorrelation_time.params[0])

In [ ]:
block_size = max(1, math.ceil(-3/compute_decorrelation_time.params[0]))
N_blocks = math.floor(t_dat_stable.size / block_size)

print("Evaluating", N_blocks, "blocks consisting of", block_size, "data points each.")

In [ ]:
sum_of_squares = 0.0
step_approximation = []

for i in range(N_blocks):
    this_block_sum = 0.0
    for j in range(block_size*i, block_size*(i+1)):
        this_block_sum += residual[j]
        
    this_block_average = this_block_sum / block_size
    sum_of_squares += this_block_average*this_block_average
    
    for k in range(block_size):
        step_approximation.append(this_block_average)

sigma_block_avg = math.sqrt(sum_of_squares / (N_blocks - 1))
print(np.asarray(step_approximation).size)
print(t_dat_stable.size)

In [ ]:
fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("t", fontsize=24, color="#322300")
ax.set_ylabel("residual of d", fontsize=24, color="#322300")

step_array = np.asarray(step_approximation)
t_array = t_dat_stable[:step_array.size]

sbn.regplot(x=t_dat_stable, y=residual, color='#a0a0a0', order=1, \
            scatter_kws={'s':1}, ci=None, truncate=False)

sbn.scatterplot(x=t_array, y=step_array, color="#e6503c", s=20)

In [ ]:
print("sigma of individual block-average data points:", sigma_block_avg)

# apply central limit theorem and divide by square root of number of blocks
sigma_whole = sigma_block_avg / math.sqrt(N_blocks)
print("sigma for whole series:", sigma_whole)

# uncertainty metric based on 2*sigma
print("\n*** 2*sigma uncertainty metric: ±", 2*sigma_whole, " ***", sep="")